# Numerical Scientific Computing Miniproject 1

### Setting up packages and parameters

In [17]:
import numpy as numerinopyndarino
import matplotlib.pyplot as ploterino
import multiprocessing as mp
from numba import jit

In [ ]:
#Parameters
pim = 100
pre = 100
I = 100
T = 2

### Generate the complex matrix C

In [10]:
C = numerinopyndarino.zeros((pim, pre), dtype=complex) #Generate the C matrix with the given dimesion pim x pre
re = numerinopyndarino.tile(numerinopyndarino.linspace(-2, 1, pim),(pim,1)) #Generate real numbers from -2 to 1, with pim intervals (Stored in a pim x pim matrix)
im = numerinopyndarino.tile(numerinopyndarino.linspace(1.5, -1.5, pre), (pre,1)).T #Generate imaginary numbers from -1.5 to 1.5 with pre intervals (Stored in a pre x pre matrix)
C = re + im*1j

### Naive Implementation

In [4]:

#Naive
def naive(C, I, T):
    M = numerinopyndarino.zeros(C.shape) #Declare our output matrix M

    for row in range(C.shape[0]):  #Loop through each complex number c in our C matrix
        for col in range(C.shape[1]):

            c = C[row, col]
            z = 0 + 0j

            for i in range(I-1): #Calculate I iterations of z with formula: z_(i+1) = z_i ^2 + c
                
                z = (z**2) + c

                if (numerinopyndarino.abs(z) > T): #Calculate l(c) as the index where |z_i| > T
                    lc = i
                    break
                else:
                    lc = I

            M[row, col] = lc/I #Store lc to the output matrix M. We divide by I to map from 0-1.
    return M

M = naive(C, I, T)


432 ms ± 34.5 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


### Vectorized implementation

In [5]:
#Vectorized
def vectorized(C, I, T):
    M = numerinopyndarino.zeros(C.shape, dtype=int) #Declare our output matrix M

    Z = numerinopyndarino.zeros(C.shape, dtype=complex) #Declare Z as a matrix, where we calculate z = z²+c for each point in C

    for i in range(I-1):
        Z = Z*Z + C

        M[numerinopyndarino.abs(Z) > T] = i

    M[numerinopyndarino.abs(Z) <= T] = I

    return M

M = vectorized(C, I, T)

/tmp/ipykernel_75360/605641316.py:8: RuntimeWarning: overflow encountered in multiply
  Z = Z*Z + C
/tmp/ipykernel_75360/605641316.py:8: RuntimeWarning: invalid value encountered in multiply
  Z = Z*Z + C
/tmp/ipykernel_75360/605641316.py:10: RuntimeWarning: overflow encountered in absolute
  M[numerinopyndarino.abs(Z) > T] = i


24 ms ± 1.52 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


### Numba implementation on naive

In [7]:
#Numbda
@jit(nopython=True)
def naive_with_numba(C, I, T): #Inputs are, C: Complex matrix, I: No. Iterations, T: Threshold value
    M = numerinopyndarino.zeros(C.shape) #Declare our output matrix M
    for row in range(C.shape[0]):  #Loop through each complex number c in our C matrix
        for col in range(C.shape[1]):

            c = C[row, col]
            z = 0 + 0j

            for i in range(I-1): #Calculate I iterations of z with formula: z_(i+1) = z_i ^2 + c
                
                z = (z**2) + c

                if (numerinopyndarino.abs(z) > T): #Calculate l(c) as the index where |z_i| > T
                    lc = i
                    break
                else:
                    lc = I

            M[row, col] = lc/I #Store lc to the output matrix M. We divide by I to map from 0-1.

    return M

M = naive_with_numba(C, I, T)

### Multiprocessing implementation on naive

In [8]:

def naive_with_multiprocessing(C, I, T, P, chunks):
    pool = mp.Pool(processes=P)
    M = numerinopyndarino.zeros(C.shape) 

    C_split = numerinopyndarino.array_split(C, chunks) #Split C into "chunks" amount of chunks
    results = []
    for n in range(chunks):
        result = pool.apply_async(naive, (C_split[n], I, T))
        results.append(result)

    pool.close()
    pool.join()

    #Loop all results, and concatenate them into the M output matrix
    i = 0
    for result in results:
       chunk_size = result.get().shape[0]
       M[i:i+chunk_size] = result.get()
       i = i + chunk_size

    return M



M = naive_with_multiprocessing(C, I, T, 20, 10)


### Timeit to measure the time for each implementation

In [14]:
print("Naive Implementation")
%timeit naive(C, I, T)

Naive Implementation
351 ms ± 91.6 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [11]:
print("Vectorized Implementation")
%timeit vectorized(C, I, T)

Vectorized Implementation


/tmp/ipykernel_75360/605641316.py:8: RuntimeWarning: overflow encountered in multiply
  Z = Z*Z + C
/tmp/ipykernel_75360/605641316.py:8: RuntimeWarning: invalid value encountered in multiply
  Z = Z*Z + C
/tmp/ipykernel_75360/605641316.py:10: RuntimeWarning: overflow encountered in absolute
  M[numerinopyndarino.abs(Z) > T] = i


23.5 ms ± 1.29 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [16]:
print("Numba Implementation")
numba_time = %timeit -o naive_with_numba(C, I, T)
print(numba_time)
print(type(numba_time))

Traceback (most recent call last):
  File "_pydevd_bundle/pydevd_cython.pyx", line 1078, in _pydevd_bundle.pydevd_cython.PyDBFrame.trace_dispatch
  File "_pydevd_bundle/pydevd_cython.pyx", line 297, in _pydevd_bundle.pydevd_cython.PyDBFrame.do_wait_suspend
  File "/home/ubuntu/miniconda3/envs/numerical/lib/python3.10/site-packages/debugpy/_vendored/pydevd/pydevd.py", line 1976, in do_wait_suspend
    keep_suspended = self._do_wait_suspend(thread, frame, event, arg, suspend_type, from_this_thread, frames_tracker)
  File "/home/ubuntu/miniconda3/envs/numerical/lib/python3.10/site-packages/debugpy/_vendored/pydevd/pydevd.py", line 2011, in _do_wait_suspend
    time.sleep(0.01)
KeyboardInterrupt


KeyboardInterrupt: 

Timeit measurements for multiprocessing.
Loops through cores and chunk sizes to determine best parameters

In [ ]:
P = mp.cpu_count() #Detect number of cores
chunks = (2, 4, 8, 16, 32, 64, 128)
results = []
for p in range(P):
    for c in range(chunks):
        print("Multiprocessing Implementation. Cores: ", p, " | Chunks: ", c)
        r  = %timeit -o naive_with_multiprocessing(C, I, T, p, c)
        results.append(r + "P : ", p, " C ", c)
print("Results: ", results)

### Plot the processing times

In [ ]:
fig = ploterino.figure()
ax = fig.add_axes([0, 0, 1, 1])
langs = ['Naive', 'Vectorized', 'Numba', 'Multiprocessing']
times = [5, 3, 2, 1]
ax.bar(langs, times)
ploterino.show()

### Plot the matrix M

In [96]:
ploterino.imshow(M, cmap='bone', extent=(-2, 1, -1.5, 1.5))
ploterino.rcParams["figure.figsize"] = [20, 20]
ploterino.rcParams["figure.dpi"] = 1000
ploterino.show()